In [1]:
from selenium import webdriver
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.common.by import By
from selenium.webdriver.support import expected_conditions as EC
import pandas as pd
import time
import json
import re
from bs4 import BeautifulSoup as bs
from urllib.parse import urlencode
import numpy as np

import threading
import json

In [2]:
# options = webdriver.FirefoxOptions()
# driver = webdriver.Firefox(options=options)
# driver.get("https://www.indeed.com/jobs?q=data+science&l=remote")
# time.sleep(1)

# soup = bs(driver.page_source, features='html.parser')

In [3]:
def get_url(query:str, location:str, offset=0):
    params = {"q":query, "l":location, "filter":0, "start":offset}
    return "https://www.indeed.com/jobs?" + urlencode(params)

In [4]:
keyword_list = ['python', 'data+science']
location_list = ['remote', 'wisconsin', 'eau+claire']

In [5]:
# job_id_list = [] # move to outside of threading
# sleeping was removed, should sleep at end of each threading session/group
def get_job_ids(driver, keyword, location, offset):
    global job_id_list
    
    indeed_jobs_url = get_url(keyword, location, offset)
    try:
        driver.get(indeed_jobs_url)
        # time.sleep(np.random.uniform(1, 2))
        response = driver.page_source  # get the html of the page
        script_tag = re.findall(r'window.mosaic.providerData\["mosaic-provider-jobcards"\]=(\{.+?\});', response)
        if script_tag is not None:
            json_blob = json.loads(script_tag[0])
            jobs_list = json_blob['metaData']['mosaicProviderJobCardsModel']['results']
            for i, job in enumerate(jobs_list):
                if job.get('jobkey') is not None:
                    job_id_list.append((job.get('jobkey'), keyword))
            # if len(jobs_list) < 10:
            #     break
    except Exception as e:
        print("Error", e)

In [15]:
options = webdriver.FirefoxOptions()
driver = webdriver.Firefox(options=options)
driver.get("https://www.indeed.com/m/basecamp/viewjob?viewtype=embdedded&jk=f27ade40cc1a3686")

In [16]:
response = driver.page_source

In [38]:
script_tag  = re.findall(r"_initialData=(\{.+?\});", response)
if script_tag is not None:
    json_blob = json.loads(script_tag[0])
    job = json_blob["jobInfoWrapperModel"]["jobInfoModel"]
    print(json_blob["salaryGuideModel"]) # this is where we get the salary info
    print(json_blob)["hiringInsightsModel"] # this is where we get the date posted info

{'acmeMicrocontentEndpoint': 'https://cocos-api.indeed.com', 'country': 'US', 'estimatedSalaryModel': {'formattedRange': '$82K - $104K a year', 'max': 103781.47, 'min': 81961.45, 'type': 'YEARLY'}, 'formattedLocation': 'King of Prussia, PA', 'jobKey': 'f27ade40cc1a3686', 'language': 'en'}


Need to add salary and date posted info to my function.

Salary need to decide which field(s) to add

Date need to decide how to store it.  When age is e.g. 'x days ago' can get today's date, subtract off the x, store that date as the date posted.

Or I could just pull daily looking only at jobs posted in the last 24 hours running the code at 12:01(1min past midnight) and setting the 'date posted' as yesterdays' date.

In [18]:
json_test = json.loads(script_tag[0])
job_test = json_test["jobInfoWrapperModel"]

In [43]:
[x for x in json_test.keys() if "hiring" in x]

['hiringInsightsModel']

In [44]:
json_test["hiringInsightsModel"]

{'age': '11 days ago',
 'employerLastReviewed': None,
 'employerResponsiveCardModel': None,
 'numOfCandidates': None,
 'postedToday': False,
 'recurringHireText': None,
 'urgentlyHiringModel': None}

In [36]:
[x for x in job_test["jobInfoModel"].keys() if "post" in (x)]

[]

In [29]:
json_test['salaryInfoModel']

In [28]:
json_test['salaryGuideModel']

{'acmeMicrocontentEndpoint': 'https://cocos-api.indeed.com',
 'country': 'US',
 'estimatedSalaryModel': {'formattedRange': '$82K - $104K a year',
  'max': 103781.47,
  'min': 81961.45,
  'type': 'YEARLY'},
 'formattedLocation': 'King of Prussia, PA',
 'jobKey': 'f27ade40cc1a3686',
 'language': 'en'}

In [30]:
job.get('jobInfoHeaderModel').keys()

dict_keys(['a11yNewtabIconActive', 'companyImagesModel', 'companyName', 'companyOverviewLink', 'companyReviewLink', 'companyReviewModel', 'employerActivity', 'employerResponsiveCardModel', 'encryptedFccCompanyId', 'formattedLocation', 'hideRating', 'isDesktopApplyButtonSticky', 'isSimpleVjImproveActive', 'isSimplifiedHeader', 'jobNormTitle', 'jobTitle', 'jobTypes', 'location', 'mobileStickyVjHeaderActive', 'openCompanyLinksInNewTab', 'parentCompanyName', 'preciseLocationModel', 'ratingsModel', 'recentSearch', 'remoteLocation', 'remoteWorkModel', 'salaryCurrency', 'salaryMax', 'salaryMin', 'salaryType', 'subtitle', 'tagModels', 'taxonomyAttributes', 'viewJobDisplay', 'workplaceInsightsModel'])

In [ ]:
# params = {"q":query, "l":location, "filter":0, "start":offset}
#     return "https://www.indeed.com/jobs?" + urlencode(params)

# threads = []
# for idx, job_element in enumerate(job_elements):
#     t = threading.Thread(args=(job_element, newdict, idx), target=parse_job) 
#     t.start()
#     threads.append(t)
    
# for t in threads:
#     t.join()

# for link_id in linkdict.values():
#     get_desc(newdict, link_id)

In [19]:
# def max # threads - remember each needs a driver
max_threads = 10
num_pages = 100
num_iters = num_pages // max_threads
keyword_list = ["python"]
location_list = ["remote"]


threads = []
options = webdriver.FirefoxOptions()
options.add_argument('-headless')  # remove if testing
driver_list = [webdriver.Firefox(options=options) for x in range(0, max_threads)] # create max_threads num of drivers
job_id_list = []
job_data = {}
for keyword in keyword_list:
    for location in location_list:
        for i in range(0, num_iters):
            for j in range(0, max_threads):
                offset = i*10*max_threads + j*10
                # print(f"Searching for {keyword} in {location} on page {offset}")
                # print(offset)
                t = threading.Thread(args=(driver_list[j], keyword, location, offset), target=get_job_ids) 
                t.start()
                threads.append(t)
                
                for t in threads:
                    t.join()
                
for i in range(0, len(job_id_list), max_threads):
    jobs_subset = job_id_list[i:i+10]
    threads = []
    for j in range(0, len(jobs_subset)):
        # print(jobs_subset)
        t = threading.Thread(args=(driver_list[j], jobs_subset[j]), target=get_job_data)
        t.start()
        threads.append(t)
        
        for t in threads:
            t.join()
for driver in driver_list:
    driver.quit()

In [20]:
job_data

{'f27ade40cc1a3686': {'terms': ['python'],
  'title': 'Software Engineer - All Levels',
  'company': 'Listrak',
  'desc': "<div>\n <p><b>About Listrak:</b></p> \n <p> We are a SaaS company that offers an integrated digital marketing platform trusted by 1,000+ leading retailers and brands for email, text message marketing, identity resolution, behavioral triggers and cross-channel orchestration. Our HQ is in Lititz, PA, but we have employees spanning over 30 states (and growing!). We are a 350-person organization led by a passionate leadership team that is invested in bringing together diverse, creative, intelligent minds to create an amazing workplace and product. Want to know more? Follow this link to check out more about our culture: https://bit.ly/ListrakRecruiting</p> \n <p><b> About the role:</b></p> \n <p> We are currently looking to add to our Product Development team with Software Engineers of all levels of experience.</p> \n <p> Listrak's Software Engineers work closely with t

In [18]:
# job_data = {}  #removed to go outside of loop for threading
def get_job_data(driver, job_id):
    global job_data
    
    if job_id[0] in job_data: # job already found from another keyword search term
        job_data[job_id[0]]['terms'].append(job_id[1]) # add the search term used to the terms 
        
    else:  # new job ID
        job_data[job_id[0]] = {}  # create empty nested dict with job id as key
        job_data[job_id[0]]['terms'] = [] # create empty list to be appended to with search terms
        try:
            indeed_job_url = "https://www.indeed.com/m/basecamp/viewjob?viewtype=embdedded&jk=" + job_id[0]
            # print(indeed_job_url)
            driver.get(indeed_job_url)
            # time.sleep(np.random.uniform(1, 2))
            response = driver.page_source
            script_tag  = re.findall(r"_initialData=(\{.+?\});", response)
            if script_tag is not None:
                json_blob = json.loads(script_tag[0])
                job = json_blob["jobInfoWrapperModel"]["jobInfoModel"]
                job_data[job_id[0]]['terms'].append(job_id[1]) # start the list of search terms with the term used here
                job_data[job_id[0]]['title'] = job.get('jobInfoHeaderModel').get('jobTitle') if job.get('jobInfoHeaderModel') is not None else ''
                job_data[job_id[0]]["company"] = job.get('jobInfoHeaderModel').get('companyName') if job.get('jobInfoHeaderModel') is not None else ''
                temp_desc = job.get('sanitizedJobDescription').strip() if job.get('sanitizedJobDescription') is not None else '' # html string
                no_html_desc = bs(temp_desc, 'html.parser').get_text(separator=' ').strip()
                job_data[job_id[0]]['desc'] = no_html_desc
                # job_data[job_id[0]]['test'] = job.get('jobDescriptionText').get('jobDescriptionText') if job.get('jobDescriptionText') is not None else ''
                

        except Exception as e:
            print("Error", e)


Try to add the salary and date posted locations to the above get_job_data() function.
Can see how I got them before in jobSearch.py, but that was using the non-clicked-in page.  Should be able to get the same from the clicked-in page too though.  Figure it out.

In [22]:
def dict_to_json(dict, filepath):
    with open(filepath, "w") as out:
        json.dump(dict, out)

In [24]:
dict_to_json(job_data,"threaded_results.json")

Once I can get the full job desc, I will want to do the following:
For each job, create a JSON object for it.  Each JSON object will have a structure like

{ "title":job_title, "company":company_name, "location":job_location, "salary":job_salary, "snippet":job_desc_snippet, "desc":full_job_desc, "tags":search_terms_used_to_find_job}

I want a way to go through and if the same job is repeated, add on to the tags in the proper json.  Can do this by instead building it as a dict, appending to the "tags" key so then search_terms_used_to_find_job is instead a list thereof, and the list is appended with the new search terms before being json-ified.

Need to figure out if I can / how to get the date posted.

Need to figure out if the job ID on indeed is unique.  If I can't figure it out, may need my own unique ID for each

Probably remove the job desc snippet since I have full descs now

Need to figure out how to go through all pages

Need to add tags for search params

Can use: https://scrapfly.io/blog/how-to-scrape-indeedcom/
To see how to better optimize this search.  Both for making searching more dynamic as well as using async IO to speed it up